In [2]:
import datetime
from datetime import datetime
import pandas as pd
import time
import requests
import os
import numpy as np
import xlsxwriter
from abc import ABCMeta, abstractmethod
from Queue import Queue
from collections import deque
import getpass
import pandas.io.formats.excel
from matplotlib import rc
import matplotlib.pyplot as plt
from universal.algos import *

/Library/Python/2.7/site-packages/statsmodels/compat/pandas.py:56: FutureWarning: The pandas.core.datetools module is deprecated and will be removed in a future version. Please use the pandas.tseries module instead.
  from pandas.core import datetools


### Simulation runner

In [16]:

class SimulationEnv(object):
    
    loggables = ['positions']
    
    def __init__(self, wealth, assets, 
                 path_to_data, start_date, end_date,
                 agent_type, expert_type, reinvest, max_assets=100):

        self.init_wealth = wealth
        self.wealth = wealth
        self.assets = assets
        self.agent_type = agent_type
        self.expert_type = expert_type
        self.path_to_data = path_to_data
        self.reinvest = reinvest
        self.max_assets = max_assets
        self.start_date = start_date
        self.end_date = end_date
        
        return
    
    ## To be called before running a simulation - initialize experts, agents, and initial position, etc.
    def setup_params(self, agent_args={}, expert_args={}):
    
        stdevs = {}
        for f in os.listdir(self.path_to_data):
            df = pd.read_csv(self.path_to_data+f)
            df = df[df["date"] < self.end_date]
            df["return"] = (df["adj_close"] - df["adj_close"].shift(1))/df["adj_close"].shift(1)
            stdevs[f] = df["return"].std()
            self.assets = [f.split(".")[0].upper() for f in sorted(stdevs, key=stdevs.get, reverse=True)[:self.max_assets]]
        
        print self.assets
        
        self.experts = [self.expert_type(a, self.path_to_data, self.start_date, self.end_date, **expert_args) for a in self.assets]
        self.agent = self.agent_type(self.experts, **agent_args)
        self.positions = np.array([weight * self.wealth for weight in self.agent.weights])
        
        return
        
    ## Run simulation
    def run(self, log=False, logpath=os.getcwd()):
        
        ## Start period counter and log
        self.period = 1
        self.finallog = []
        self.log = log
        self.logpath = logpath
        
        ## Warmup period: 
        ## i.e. for strategies involving moving average indicators, wait until we have enough data to calculate MA
        for expert in self.agent.experts:
            expert.warmup()
        
        ## Simulation: Go until data iterators reach the end
        print "Initial weights:"
        print np.array([weight for weight in self.agent.weights])
        
        while True:
            try:
                print "PERIOD {}".format(self.period)
                print "dates:"
                dates = [e.current_date for e in self.agent.experts]
                print list(set(dates))
                ## NEED TO MAKE THIS TRUE
                ## assert len(set(dates)) == 1
              


                print "---------------------"
                ## Log this period
                if log:
                    self.logperiod()
                    
                ## Update experts with last period's rewards
                for i, expert in enumerate(self.agent.experts):
                    expert.update()
                    
                
                    
                ## Update agent accordingly (i.e. for Hedge, update weights according to each expert's reward in the last period)
                self.agent.update()
                           
                ## Rewards accrue to agent
                self.positions = self.positions * (1 + self.agent.returns)
                self.wealth = np.sum(self.positions)
                
                ## Rebalance according to new, updated weights
                ## TODO: only allow non-fractional shares to be purchased (?)
                if np.sum(self.agent.weights) == 1:
                    self.positions = np.array([weight * self.wealth for weight in self.agent.weights])
                
#                 print "weights:"
#                 print np.array([weight for weight in self.agent.weights])

#                 print "rewards:"
#                 print np.array([r for r in self.agent.rewards])
#                 print "returns:"
#                 print np.array([r for r in self.agent.returns])
                
#                 print "positions:"
#                 print np.array([weight * self.wealth for weight in self.agent.weights])
#                 print "positions invested:"
                positions_invested = np.array([e.pick for e in self.agent.experts])*self.positions
#                 print positions_invested

                if self.reinvest and np.any(positions_invested):
                    uninvested_wealth = self.wealth - np.sum(positions_invested)
                    print "Need to reallocate {} cash amongst experts that are investing".format(uninvested_wealth)
                    print "Total wealth:"
                    print self.wealth
                    print "Reinvestments:"
                    print uninvested_wealth * positions_invested/np.sum(positions_invested)
                    print "Final position"
                    self.positions = uninvested_wealth * positions_invested/np.sum(positions_invested) + positions_invested
                    print self.positions
                    new_wealth = np.sum(self.positions)
                    assert(new_wealth-self.wealth <= 0.00001)
                
#                 print "---------------------"
#                 print "\n\n"
                
                
                ## Advance period
                self.period += 1
                
            except StopIteration:
                break
        
        ## Write the log file
        if log:
            self.savelog()

    def logperiod(self):
        row = [self.period] + [self.wealth]
        nrow = []
        for loggable in (self.loggables):
            if getattr(self,loggable) is None:
                nrow += [None] * len(self.experts)
            else:
                nrow += getattr(self,loggable).tolist()
        arow = []
        for loggable in (self.agent_type.loggables):
            if getattr(self.agent,loggable) is None:
                arow += [None] * len(self.experts)
            else:
                arow += getattr(self.agent,loggable).tolist()
        erow = []
        for loggable in (self.expert_type.loggables):
            if [getattr(e,loggable) for e in self.experts] is None:
                erow += [None] * len(self.experts)
            else:
                erow += [getattr(e,loggable) for e in self.experts]
        row += nrow + arow + erow
        self.finallog.append(row)
    
    def savelog(self):
        # Set up log file structure
        runtime = datetime.datetime.now()
        runuser = getpass.getuser()
        logname = runuser + "_" + runtime.strftime('%Y-%m-%d_%H-%M-%S')
        if not os.path.exists(os.path.join(self.logpath, logname)):
            os.makedirs(os.path.join(self.logpath, logname))
            os.makedirs(os.path.join(self.logpath, logname, 'plots'))
        
        # Create dataframe from log
        col = ['period', 'wealth'] + \
            [x+'.'+y for x in self.loggables for y in self.assets] + \
            [x+'.'+y for x in self.agent_type.loggables for y in self.assets] + \
            [x+'.'+y for x in self.expert_type.loggables for y in self.assets]
        df = pd.DataFrame(self.finallog, columns=col)
        df.set_index('period', inplace=True)
        
        # Write xlsx of log data
        writer = pd.ExcelWriter(os.path.join(self.logpath, logname, logname+'.xlsx'), engine='xlsxwriter')
        pd.io.formats.excel.header_style = None
        df.to_excel(writer,'run_log')
        
        workbook  = writer.book
        worksheet = writer.sheets['run_log']
        
        header_format = workbook.add_format({'bold': True,'text_wrap': True})
        worksheet.set_row(0, None, header_format)
        writer.save()
        
        # Set up matplotlib. Loop through loggables and save a plot with and without legend for each.
        rc('font', family = 'serif', serif = 'cmr10')
        plots = ['wealth'] + self.loggables + self.agent_type.loggables + self.expert_type.loggables
        
        for p in plots:
            for legend in [True, False]:
                plotdf = df.filter(regex='period|'+p)
                plotlab = [l.split(p+'.',1)[1] if l != 'wealth' else l.title() for l in list(plotdf.columns.values)]
                plt.plot(plotdf)
                plt.ylabel(p.title())
                plt.xlabel('Round')
                plt.ticklabel_format(useOffset=False)
                if legend:
                    plt.legend(plotlab, loc=9, bbox_to_anchor=(0.5, -0.15), ncol=4)
                    plt.savefig(os.path.join(self.logpath, logname, 'plots', p+'_legend.png'), bbox_inches='tight', dpi=300)
                else:
                    plt.savefig(os.path.join(self.logpath, logname, 'plots', p+'.png'), bbox_inches='tight', dpi=300)
                plt.close()



### Base classes

Base classes for agents and experts to be implemented by us

In [7]:

class Agent(object):
    __metaclass__ =ABCMeta
    
    @abstractmethod
    def __init__(self):
        pass
    
    @abstractmethod
    def update(self):
        pass
    
    @abstractmethod
    def act(self):
        pass
    
class Expert(object):
    __metaclass__=ABCMeta
    
    ## Required parameters for initializing experts
    @abstractmethod
    def __init__(self, name, path_to_data, start_date, end_date):
        self.reward = 0.
        self.pick = False ## Need to activate experts in child classes
        self.data = pd.read_csv(path_to_data + name + ".csv", iterator=True, chunksize=1)
        self.current_date = datetime.strptime("1000-01-01", "%Y-%m-%d")
        self.start_date = datetime.strptime(start_date, "%Y-%m-%d")
        self.end_date = datetime.strptime(end_date, "%Y-%m-%d")
        while self.current_date < self.start_date:
            self.last_row = self.data.get_chunk(1)
            self.last_price = float(self.last_row["adj_close"])
            self.current_date = datetime.strptime(self.last_row["date"].item(), "%Y-%m-%d")
        
    @abstractmethod
    def update(self):
        pass
    
class Context(object):
    __metaclass__=ABCMeta
    
    @abstractmethod
    def __init__(self, context_data):
        pass
    
    @abstractmethod
    def observe(self):
        pass

### Agents

Implementations of different online portfolio selection algorithms
* Exponential Gradient
* Exponential Gradient (recent history only)

In [8]:
## EG. (http://www.cis.upenn.edu/~mkearns/finread/helmbold98line.pdf)
class EG(Agent):
    
    loggables = ['returns','rewards','weights']
    
    ## Initialize with a set of experts
    def __init__(self, experts, eta):
        self.eta = eta
        self.experts = experts
        self.weights = np.ones(len(self.experts))/len(self.experts)
        self.rewards = None
        self.returns = None
        return
    
    ## Update the agent's rewards and its weights for each expert
    def update(self):
        self.rewards = np.asarray([e.reward for e in self.experts])
        self.returns = np.asarray([e.returns for e in self.experts])
        multipliers = np.exp(self.eta * self.rewards/np.sum(self.weights * self.rewards))
        self.weights = (self.weights * multipliers)/ np.sum(self.weights * multipliers)
        self.weights = np.nan_to_num(self.weights)

        return
    
    def act(self):
        return self.weights


class EGRecent(Agent):
    
    loggables = ['returns','rewards','weights']
    
    ## Initialize with a set of experts
    def __init__(self, experts, eta, n):
        self.eta = eta
        self.experts = experts
        #self.weights = Queue(maxsize=n)
        self.weights = np.ones(len(self.experts))/len(self.experts)
        self.rewards = deque(maxlen=n)
        self.returns = None
        self.t = 0
        self.n = n
        #self.rewards = None
        #self.returns = None
        return
    
    ## Update the agent's rewards and its weights for each expert
    def update(self):
           
        self.rewards.append(np.asarray([e.reward for e in self.experts]))
        self.returns = np.asarray([e.returns for e in self.experts])
        
        self.weights = np.ones(len(self.experts))/len(self.experts)
        #print self.t
        #print len(self.rewards)
        for rewards in self.rewards:
            rewards = np.asarray(rewards)
            multipliers = np.exp(self.eta * rewards/np.sum(self.weights * rewards))
            self.weights = (self.weights * multipliers)/ np.sum(self.weights * multipliers)
            self.weights = np.nan_to_num(self.weights)
        self.t += 1
        #print self.t
        
        return
    
    def act(self):
        return self.weights
    
      
        

More agents to serve as naive/benchmark portfolio allocation algorithms:
* Equal-weighted buy and hold
* Market-weighted buy and hold
* Constantly rebalanced portfolio


In [9]:
## Some other examples of agents to use as benchmarks 

class ConstantRebalancer(Agent):
    
    loggables = ['rewards','weights']
    
    def __init__(self, experts):
        self.experts = experts
        self.weights = np.ones(len(self.experts))/len(self.experts)
        self.rewards = None
        return
    
    def update(self):
        self.rewards = np.asarray([e.reward for e in self.experts])
        self.returns = self.rewards - 1.
        return
    
    def act(self):
        return self.weights

class BestConstantRebalancer(Agent):
    
    loggables = ['rewards','weights']
    
    def __init__(self, experts, weights):
        self.experts = experts
        self.weights = weights
        self.rewards = None
        return
    
    def update(self):
        self.rewards = np.asarray([e.reward for e in self.experts])
        self.returns = self.rewards - 1.
        return
    
    def act(self):
        return self.weights
    
## to be used with "Dummy" Expert for each stock
class WeightedBuyHold(Agent):
    
    def __init__(self, experts):
        self.experts = experts
        self.weights = np.asarray([e.last_price for e in self.experts])
        self.weights = [float(w)/sum(self.weights) for w in self.weights]
        self.rewards = None
        return
    
    def update(self):
        self.rewards = np.asarray([e.reward for e in self.experts])
        self.returns = self.rewards - 1.
        self.weights = np.multiply(self.weights, self.rewards)
        self.weights = np.divide(self.weights, np.sum(self.weights))
        assert((np.sum(self.weights) - 1.) <= 0.00001)        
        return
    
    def act(self):
        return self.weights 

## to be used with "Dummy" Expert for each stock    
class RandomWeightedBuyHold(Agent):
    
    def __init__(self, experts):
        self.experts = experts
        self.weights = np.random.dirichlet(np.ones(len(self.experts)), size=1)
        self.rewards = None
        return
    
    def update(self):
        self.rewards = np.asarray([e.reward for e in self.experts])
        self.returns = self.rewards - 1.
        self.weights = np.multiply(self.weights, self.rewards)
        self.weights = np.divide(self.weights, np.sum(self.weights))
        assert((np.sum(self.weights) - 1.) <= 0.00001)
        return
    
    def act(self):
        return self.weights 
    

## to be used with "Dummy" Expert for each stock
class NaiveBuyHold(Agent):
    
    def __init__(self, experts):
        self.experts = experts
        self.weights = np.ones(len(self.experts))/len(self.experts)
        self.rewards = None
        return
    
    def update(self):
        self.rewards = np.asarray([e.reward for e in self.experts])
        self.returns = self.rewards - 1.
        self.weights = np.multiply(self.weights, self.rewards)
        self.weights = np.divide(self.weights, np.sum(self.weights))
        assert((np.sum(self.weights) - 1.) <= 0.00001)
        return
    
    def act(self):
        return self.weights

### Experts

* Dummy
* Mean Reversion
* Momentum

In [10]:

## Dummy expert that always pick the same asset
class Dummy(Expert):
    
    loggables = ['reward']
    
    ## Expert has a reward associated with its pick
    def __init__(self, name, path_to_data, start_date, end_date):
        super(Dummy, self).__init__(name, path_to_data, start_date, end_date)
        self.pick = True
        return
    
    ## Expert updates its reward 
    def update(self):
        self.last_row = self.data.get_chunk(1)
        self.current_date = datetime.strptime(self.last_row["date"].item(), "%Y-%m-%d")
        
        if self.current_date > self.end_date:
            raise StopIteration
            
        current_price = float(self.last_row["adj_close"])
        self.reward = current_price/self.last_price
        self.returns = self.reward - 1.
        self.last_price = current_price
        return
    
    def warmup(self):
        pass
    

class MeanReversion(Expert):
    
    loggables = ['avg','std']
    
    def __init__(self, name, path_to_data, start_date, end_date, window_size, threshold):
        super(MeanReversion, self).__init__(name, path_to_data, start_date, end_date)
        self.window_size = window_size
        self.avg = 0.0
        self.std = 0.0
        self.threshold = threshold
        self.last_n_prices = Queue(maxsize=10)
        self.returns = 0.

        return
    
    def warmup(self):
        n = 1
        while n <= self.window_size:
            self.last_n_prices.put(self.last_price)
            
            self.last_row = self.data.get_chunk(1)
            self.current_date = datetime.strptime(self.last_row["date"].item(), "%Y-%m-%d")

            self.last_price = float(self.last_row["adj_close"])
            n += 1
        return
        
    def update(self):
        _ = self.last_n_prices.get()
        
        self.last_n_prices.put(self.last_price)
        self.avg = np.mean(list(self.last_n_prices.queue))
        self.std = np.std(list(self.last_n_prices.queue))
        
        self.last_row = self.data.get_chunk(1)
        self.current_date = datetime.strptime(self.last_row["date"].item(), "%Y-%m-%d")
        
        if self.current_date > self.end_date:
            raise StopIteration
            
        current_price = float(self.last_row["adj_close"])
        
        ## If self.pick is True, we bought the stock and our reward is whatever the return was in the last period
        if self.pick:
            self.reward = current_price/self.last_price
            self.returns = self.reward - 1.
        else:
            self.reward = self.last_price/current_price
            self.returns = 0
            
        self.last_price = current_price

        if self.last_price <= self.avg - self.threshold * self.std:
            self.pick = True
        else:
            self.pick = False

        return

    
# class Momentum(Expert):
    
#     loggables = ['avg','std']
    
#     def __init__(self, name, path_to_data, window_size, threshold):
#         self.reward = 0.
#         self.pick = False
#         self.data = pd.read_csv(path_to_data + name + ".csv", iterator=True, chunksize=1)
#         self.last_price = float(self.data.get_chunk(1)["adj_close"])
#         self.window_size = window_size
#         self.avg = 0.0
#         self.std = 0.0
#         self.threshold = threshold
#         self.last_n_prices = Queue(maxsize=10)
#         self.returns = 0.
#         return
    
#     def warmup(self):
#         n = 1
#         while n <= self.window_size:
#             self.last_n_prices.put(self.last_price)
#             self.last_price = float(self.data.get_chunk(1)["adj_close"])
#             n += 1
#         return
        
#     def update(self):
#         _ = self.last_n_prices.get()
            
#         self.last_n_prices.put(self.last_price)
#         self.avg = np.mean(list(self.last_n_prices.queue))
#         self.std = np.std(list(self.last_n_prices.queue))
        
#         current_price = float(self.data.get_chunk(1)["adj_close"])

#         ## If self.pick is True, we bought the stock and our reward is whatever the return was in the last period
#         if self.pick:
#             self.reward = current_price/self.last_price
#             self.returns = self.reward - 1.
#         else:
#             self.reward = -current_price/self.last_price
#             self.returns = 0
#         self.last_price = current_price

#         if self.last_price >= self.avg - self.threshold * self.std:
#             self.pick = True
#         else:
#             self.pick = False

#         return
  

### Contexts

In [17]:
def GridSearch(Agent, Expert, reinvest=False, full_data=False, agent_args=[], expert_args=[]):
    ## Run simulation 
    start = time.time()
    if full_data:
        data = "data/djia_20000101_20171101/"
        start_date = "2000-01-01"
        year = 17.
    else:
        data = "data/djia_20150101_20171101/"
        start_date = "2015-01-01"
        year = 2.
    best_wealth = 0
    best_params = {}
    for agent_arguments in agent_args:
        for expert_arguments in expert_args:
            
            s = SimulationEnv(
                initial_wealth, 
                stocks, 
                data, 
                start_date,
                "2017-11-01", 
                Agent, 
                Expert, 
                reinvest
            )
            s.setup_params(
                agent_args=agent_arguments,
                expert_args=expert_arguments
            )
            s.run()

            years = year + 11./12
            ar = ((s.wealth)/initial_wealth)**(1/years) - 1
            end = time.time()

            if s.wealth > best_wealth:
                best_wealth = s.wealth
                best_params = {
                    "agent_args": agent_arguments,
                    "expert_args": expert_arguments,
                    "Initial wealth": initial_wealth,
                    "Final wealth": s.wealth,
                    "Annualized return": ar,
                    "Time": int(end-start),
                }
    print("Best params:", best_params)
    

GridSearch(ConstantRebalancer, Dummy, reinvest=True, full_data=False, agent_args=[{}], expert_args=[{}])
GridSearch(EG, Dummy, reinvest=True, full_data=False, agent_args=[{"eta":-0.01},{"eta":-0.005}], expert_args=[{}])


['CAT', 'DD', 'GS', 'AAPL', 'MSFT', 'CVX', 'NKE', 'INTC', 'BA', 'JPM', 'AXP', 'CSCO', 'UNH', 'MRK', 'GE', 'V', 'IBM', 'WMT', 'XOM', 'DIS', 'HD', 'PFE', 'UTX', 'TRV', 'MCD', 'VZ', 'MMM', 'JNJ', 'PG', 'KO']
Initial weights:
[ 0.03333333  0.03333333  0.03333333  0.03333333  0.03333333  0.03333333
  0.03333333  0.03333333  0.03333333  0.03333333  0.03333333  0.03333333
  0.03333333  0.03333333  0.03333333  0.03333333  0.03333333  0.03333333
  0.03333333  0.03333333  0.03333333  0.03333333  0.03333333  0.03333333
  0.03333333  0.03333333  0.03333333  0.03333333  0.03333333  0.03333333]
PERIOD 1
dates:
[datetime.datetime(2015, 1, 2, 0, 0)]
---------------------
Need to reallocate 3.33066907388e-16 cash amongst experts that are investing
Total wealth:
0.982946438703
Reinvestments:
[  1.11022302e-17   1.11022302e-17   1.11022302e-17   1.11022302e-17
   1.11022302e-17   1.11022302e-17   1.11022302e-17   1.11022302e-17
   1.11022302e-17   1.11022302e-17   1.11022302e-17   1.11022302e-17
   1.110

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.978395560231
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03261319  0.03261319  0.03261319  0.03261319  0.03261319  0.03261319
  0.03261319  0.03261319  0.03261319  0.03261319  0.03261319  0.03261319
  0.03261319  0.03261319  0.03261319  0.03261319  0.03261319  0.03261319
  0.03261319  0.03261319  0.03261319  0.03261319  0.03261319  0.03261319
  0.03261319  0.03261319  0.03261319  0.03261319  0.03261319  0.03261319]
PERIOD 10
dates:
[datetime.datetime(2015, 1, 15, 0, 0)]
---------------------
Need to reallocate 1.11022302463e-16 cash amongst experts that are investing
Total wealth:
0.988740014441
Reinvestments:
[  3.70074342e-18   3.70074342e-18   3.70074342e-18   3.70074342e-18
   3.70074342e-18   3.70074342e-18   3.70074342e-18   3.70074342e-18
   3.70074342e-18   3.70074342e-18   3.70074342e-18 

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.992676932638
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03308923  0.03308923  0.03308923  0.03308923  0.03308923  0.03308923
  0.03308923  0.03308923  0.03308923  0.03308923  0.03308923  0.03308923
  0.03308923  0.03308923  0.03308923  0.03308923  0.03308923  0.03308923
  0.03308923  0.03308923  0.03308923  0.03308923  0.03308923  0.03308923
  0.03308923  0.03308923  0.03308923  0.03308923  0.03308923  0.03308923]
PERIOD 22
dates:
[datetime.datetime(2015, 2, 3, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.992290724675
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03307636  0.03307636  0.03307636  0.03307636  0.03307636  0.033

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
1.01997673258
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03399922  0.03399922  0.03399922  0.03399922  0.03399922  0.03399922
  0.03399922  0.03399922  0.03399922  0.03399922  0.03399922  0.03399922
  0.03399922  0.03399922  0.03399922  0.03399922  0.03399922  0.03399922
  0.03399922  0.03399922  0.03399922  0.03399922  0.03399922  0.03399922
  0.03399922  0.03399922  0.03399922  0.03399922  0.03399922  0.03399922]
PERIOD 31
dates:
[datetime.datetime(2015, 2, 17, 0, 0)]
---------------------
Need to reallocate -2.22044604925e-16 cash amongst experts that are investing
Total wealth:
1.01925684382
Reinvestments:
[ -7.40148683e-18  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18
  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18
  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18  

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
1.03420638888
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03447355  0.03447355  0.03447355  0.03447355  0.03447355  0.03447355
  0.03447355  0.03447355  0.03447355  0.03447355  0.03447355  0.03447355
  0.03447355  0.03447355  0.03447355  0.03447355  0.03447355  0.03447355
  0.03447355  0.03447355  0.03447355  0.03447355  0.03447355  0.03447355
  0.03447355  0.03447355  0.03447355  0.03447355  0.03447355  0.03447355]
PERIOD 40
dates:
[datetime.datetime(2015, 3, 2, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
1.02937723954
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03431257  0.03431257  0.03431257  0.03431257  0.03431257  0.03431

...

Need to reallocate -2.22044604925e-16 cash amongst experts that are investing
Total wealth:
0.949530509287
Reinvestments:
[ -7.40148683e-18  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18
  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18
  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18
  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18
  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18
  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18
  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18  -7.40148683e-18
  -7.40148683e-18  -7.40148683e-18]
Final position
[ 0.03165102  0.03165102  0.03165102  0.03165102  0.03165102  0.03165102
  0.03165102  0.03165102  0.03165102  0.03165102  0.03165102  0.03165102
  0.03165102  0.03165102  0.03165102  0.03165102  0.03165102  0.03165102
  0.03165102  0.03165102  0.03165102  0.03165102  0.03165102  0.03165102
  0.03165102  0.03165102  0.03165102  0.03165102  0.

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.979272154758
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03264241  0.03264241  0.03264241  0.03264241  0.03264241  0.03264241
  0.03264241  0.03264241  0.03264241  0.03264241  0.03264241  0.03264241
  0.03264241  0.03264241  0.03264241  0.03264241  0.03264241  0.03264241
  0.03264241  0.03264241  0.03264241  0.03264241  0.03264241  0.03264241
  0.03264241  0.03264241  0.03264241  0.03264241  0.03264241  0.03264241]
PERIOD 287
dates:
[datetime.datetime(2016, 2, 29, 0, 0), datetime.datetime(2016, 2, 23, 0, 0)]
---------------------
Need to reallocate 3.33066907388e-16 cash amongst experts that are investing
Total wealth:
0.982936987693
Reinvestments:
[  1.11022302e-17   1.11022302e-17   1.11022302e-17   1.11022302e-17
   1.11022302e-17   1.11022302e-17   1.11022302e-17   1.11022302e-17
   1.11022302

Need to reallocate 2.22044604925e-16 cash amongst experts that are investing
Total wealth:
1.01308933475
Reinvestments:
[  7.40148683e-18   7.40148683e-18   7.40148683e-18   7.40148683e-18
   7.40148683e-18   7.40148683e-18   7.40148683e-18   7.40148683e-18
   7.40148683e-18   7.40148683e-18   7.40148683e-18   7.40148683e-18
   7.40148683e-18   7.40148683e-18   7.40148683e-18   7.40148683e-18
   7.40148683e-18   7.40148683e-18   7.40148683e-18   7.40148683e-18
   7.40148683e-18   7.40148683e-18   7.40148683e-18   7.40148683e-18
   7.40148683e-18   7.40148683e-18   7.40148683e-18   7.40148683e-18
   7.40148683e-18   7.40148683e-18]
Final position
[ 0.03376964  0.03376964  0.03376964  0.03376964  0.03376964  0.03376964
  0.03376964  0.03376964  0.03376964  0.03376964  0.03376964  0.03376964
  0.03376964  0.03376964  0.03376964  0.03376964  0.03376964  0.03376964
  0.03376964  0.03376964  0.03376964  0.03376964  0.03376964  0.03376964
  0.03376964  0.03376964  0.03376964  0.03376964  0.03

Total wealth:
1.04924214799
Reinvestments:
[  1.48029737e-17   1.48029737e-17   1.48029737e-17   1.48029737e-17
   1.48029737e-17   1.48029737e-17   1.48029737e-17   1.48029737e-17
   1.48029737e-17   1.48029737e-17   1.48029737e-17   1.48029737e-17
   1.48029737e-17   1.48029737e-17   1.48029737e-17   1.48029737e-17
   1.48029737e-17   1.48029737e-17   1.48029737e-17   1.48029737e-17
   1.48029737e-17   1.48029737e-17   1.48029737e-17   1.48029737e-17
   1.48029737e-17   1.48029737e-17   1.48029737e-17   1.48029737e-17
   1.48029737e-17   1.48029737e-17]
Final position
[ 0.03497474  0.03497474  0.03497474  0.03497474  0.03497474  0.03497474
  0.03497474  0.03497474  0.03497474  0.03497474  0.03497474  0.03497474
  0.03497474  0.03497474  0.03497474  0.03497474  0.03497474  0.03497474
  0.03497474  0.03497474  0.03497474  0.03497474  0.03497474  0.03497474
  0.03497474  0.03497474  0.03497474  0.03497474  0.03497474  0.03497474]
PERIOD 307
dates:
[datetime.datetime(2016, 3, 22, 0, 0), 

KeyboardInterrupt: 

In [8]:
  
class VolContext(Context):
    
    def __init__(self, data_file, threshold):
        self.data = pd.read_csv(data_file, iterator=True, chunksize=1)
        self.threshold = threshold
        self.contexts = ["HighVol", "LowVol"]
        return
    
    # Returns a string giving the name of the context
    def observe(self):
        if float(self.data.get_chunk(1)["adj_close"]) > self.threshold:
            return self.contexts[0]
        else:
            return self.contexts[1]

### Best Constant Rebalanced Portfolio (BCRP)

BCRP as benchmark, weights are constant in time and are determined in hindsight for determining the best possible return.

In [5]:
from pandas_datareader import data, wb

def BestCRP(path_to_data, start_date, end_date, initial_wealth):
    start = time.time()
    list_ = []
    i = 0
    for f in os.listdir(path_to_data):
        ticker = os.path.splitext(f)[0].upper()
        if i == 0:
            df = pd.read_csv(path_to_data+f, usecols=["date"])
            df = df[df["date"] > start_date]
            df = df[df["date"] < end_date]
            a = df[["date"]]
            a["date"] = pd.to_datetime(a["date"])
            list_.append(a)
        df = pd.read_csv(path_to_data+f, usecols=["adj_close"])
        df.columns = [ticker]
        list_.append(df[[ticker]])
        i+=1

    frame = pd.concat(list_, axis=1)
    frame = frame.set_index("date")
    wS = frame.resample('W').last()
    algo = BCRP()
    result = algo.run(wS)
    end = time.time()

#     print result.summary()
    print "Initial wealth: ${}".format(initial_wealth)
    print "Final wealth: ${}".format(result.total_wealth)
    print "Annualized return: {}".format(result.annualized_return)
    print "Time: {}s".format(int(end-start))
    

BestCRP("data/djia_20000101_20170831/", "2000-01-01", "2017-08-31", 1.)

Initial wealth: $1.0
Final wealth: $66.0179468438
Annualized return: 0.267713276023
Time: 0s


In [12]:
stocks = ['AAPL', 'AXP', 'BA', 'CAT', 'CSCO', 'CVX', 'DD', 'DIS', 'GE',
 'GS', 'HD', 'IBM', 'INTC', 'JNJ', 'JPM', 'KO', 'MCD', 'MMM', 
'MRK', 'MSFT', 'NKE', 'PFE', 'PG', 'TRV', 'UNH', 'UTX', 'VZ', 'WMT', 'XOM']
stocks = [stock.lower() for stock in stocks]

In [13]:
initial_wealth = 1.

In [82]:
## Run simulation where constantly rebalance investments
start = time.time()
s = SimulationEnv(1., stocks, "data/djia_20150101_20171101/", "2016-01-01", "2016-12-31", EG, Dummy, False, max_assets=2)
s.setup_params(agent_args={"eta": 0.01})
s.run()

years = 2. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print("Initial wealth: ${}".format(initial_wealth))
print("Final wealth: ${}".format(s.wealth))
print("Annualized return: {}".format(ar))
print("Time: {}s".format(int(end-start)))

In [79]:
# Run simulation with sophisticated experts and fully invested wealth
start = time.time()
s = SimulationEnv(1., stocks, "data/djia_20000101_20171101/", "2000-01-01", "2017-11-01", EG, MeanReversion, reinvest=True, max_assets=15)
s.setup_params(
    agent_args={"eta": 0.01}, 
    expert_args={"window_size": 10, "threshold": .5})
s.run()

years = 17. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print("Initial wealth: ${}".format(initial_wealth))
print("Final wealth: ${}".format(s.wealth))
print("Annualized return: {}".format(ar))
print("Time: {}s".format(int(end-start)))

Initial wealth: $1.0
Final wealth: $3.99557828344
Annualized return: 0.0803800058262
Time: 111s


In [14]:
## Run simulation where constantly rebalance investments
start = time.time()
s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20171101/", "2000-01-01", "2017-11-01", NaiveBuyHold, Dummy, True)
s.setup_params(agent_args={})
s.run()

years = 17. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print("Initial wealth: ${}".format(initial_wealth))
print("Final wealth: ${}".format(s.wealth))
print("Annualized return: {}".format(ar))
print("Time: {}s".format(int(end-start)))

OSError: [Errno 2] No such file or directory: 'data/djia_20000101_20171101/'

In [84]:
## Run simulation where constantly rebalance investments
start = time.time()
s = SimulationEnv(initial_wealth, stocks, "data/djia_20150101_20171101/", "2015-01-01", "2017-11-01", ConstantRebalancer, Dummy, True)
s.setup_params(agent_args={})
s.run()

years = 2. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print("Initial wealth: ${}".format(initial_wealth))
print("Final wealth: ${}".format(s.wealth))
print("Annualized return: {}".format(ar))
print("Time: {}s".format(int(end-start)))

In [ ]:
## Run simulation where constantly rebalance investments
start = time.time()
s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20171101/", "2000-01-01", "2017-11-01", ConstantRebalancer, Dummy, True)
s.setup_params(expert_args={"eta": -0.01})
s.run()

years = 17. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print("Initial wealth: ${}".format(initial_wealth))
print("Final wealth: ${}".format(s.wealth))
print("Annualized return: {}".format(ar))
print("Time: {}s".format(int(end-start)))

In [ ]:
## Run a simulation with Hedge, each expert is a proxy for buying a given stock
start = time.time()

s = SimulationEnv(initial_wealth, stocks, "data/djia_20150101_20171101/", "2015-01-01", "2017-11-01", EG, Dummy, True)
s.setup_params(agent_args = {"eta": -0.01})
s.run(log=True, logpath="logs")

years = 2. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [ ]:
## Run a simulation with Hedge, each expert is a proxy for buying a given stock
start = time.time()

s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20171101/", "2000-01-01", "2017-11-01", EG, Dummy, True)
s.setup_params(agent_args = {"eta": -0.01})
s.run()

years = 17. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [ ]:
## Run a simulation with Hedge, each expert is a proxy for buying a given stock

s = SimulationEnv(initial_wealth, stocks, "data/djia_20150101_20171101/", "2015-01-01", "2017-11-01", EGRecent, Dummy, True)
s.setup_params(agent_args = {"eta": -0.01, "n": 100})
s.run()

years = 2. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [ ]:
## Run a simulation with Hedge, each expert is a proxy for buying a given stock

s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20171101/", "2000-01-01", "2017-11-01", EGRecent, Dummy, True)
s.setup_params(agent_args = {"eta": -0.01, "n": 750})
s.run()

years = 17. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [ ]:
## Run simulation where we just buy and hold all stocks in equal amounts
start = time.time()
s = SimulationEnv(initial_wealth, stocks, "data/djia_20150101_20171101/", "2015-01-01", "2017-11-01", NaiveBuyHold, Dummy, True)
s.setup_params(expert_args={})
s.run()

years = 2. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))



In [ ]:
## Run simulation where we just buy and hold all stocks in equal amounts
start = time.time()
s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20171101/", "2000-01-01", "2017-11-01", NaiveBuyHold, Dummy, True)
s.setup_params(expert_args={})
s.run()

years = 17. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [ ]:
## Run simulation where we each expert only recommends to buy when the price crosses 0.5 standard deviations below the 10-day moving average. 
## Otherwise doesn't do anything
## Sell position when price gets above 0.5 standard deviations below the 10-day MA

start = time.time()

s = SimulationEnv(initial_wealth, stocks, "data/djia_20150101_20171101/", "2015-01-01", "2017-11-01", EG, MeanReversion, True)

s.setup_params(
    agent_args={"eta": -0.01},
    expert_args={"window_size": 10, "threshold": .5}
)

s.run()
end = time.time()
years = 2. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [ ]:

start = time.time()

s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20171101/", "2000-01-01", "2017-11-01", EG, MeanReversion, True)

s.setup_params(
    agent_args={"eta": -0.01},
    expert_args={"window_size": 10, "threshold": .5}
)

s.run()
end = time.time()
years = 17. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [ ]:

start = time.time()

s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20171101/", "2000-01-01", "2017-11-01", EGRecent, MeanReversion, True)

s.setup_params(
    agent_args={"eta": -0.01, "n": 1250},
    expert_args={"window_size": 10, "threshold": .5}
)

s.run()
end = time.time()
years = 17. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [ ]:
start = time.time()
s = SimulationEnv(initial_wealth, stocks, "data/djia_20150101_20171101/", "2015-01-01", "2017-11-01", EG, Momentum, True)

years = 2. + 11./12
s.setup_params(
    agent_args={"eta": -0.01},
    expert_args={"window_size": 10, "threshold": 2.5}
)

s.run()
end = time.time()

ar = ((s.wealth)/initial_wealth)**(1/years) - 1

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [ ]:
start = time.time()
s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20171101/", "2000-01-01", "2017-11-01", EG, Momentum, True)

years = 17. + 11./12
s.setup_params(
    agent_args={"eta": -0.01},
    expert_args={"window_size": 10, "threshold": 2.5}
)

s.run()
end = time.time()

ar = ((s.wealth)/initial_wealth)**(1/years) - 1

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [ ]:
start = time.time()
s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20171101/", "2000-01-01", "2017-11-01", EGRecent, Momentum, True)

years = 17. + 11./12
s.setup_params(
    agent_args={"eta": -0.001, "n": 500},
    expert_args={"window_size": 10, "threshold": 2.5}
)

s.run()
end = time.time()

ar = ((s.wealth)/initial_wealth)**(1/years) - 1

print "Initial wealth: ${}".format(initial_wealth)
print "Final wealth: ${}".format(s.wealth)
print "Annualized return: {}".format(ar)
print "Time: {}s".format(int(end-start))

In [18]:
## Run buy-and-hold simulation, where initial weights are determined by respective stocks' Dow Jones Index
start = time.time()
s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20170831/", "2000-01-01", "2017-08-31", WeightedBuyHold, Dummy, True)
s.setup_params(agent_args={})
s.run()

years = 17. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print("Initial wealth: ${}".format(initial_wealth))
print("Final wealth: ${}".format(s.wealth))
print("Annualized return: {}".format(ar))
print("Time: {}s".format(int(end-start)))

['INTC', 'AAPL', 'JPM', 'CSCO', 'GS', 'AXP', 'CAT', 'UNH', 'HD', 'MSFT', 'DIS', 'GE', 'NKE', 'BA', 'DD', 'MRK', 'UTX', 'IBM', 'CVX', 'PFE', 'VZ', 'XOM', 'WMT', 'MCD', 'MMM', 'PG', 'KO', 'JNJ']
Initial weights:
[ 0.03416236  0.00420026  0.032796    0.05216429  0.08589196  0.04220621
  0.01749989  0.00694262  0.05423487  0.04530987  0.0278417   0.03387525
  0.00557374  0.0317435   0.03992874  0.03984824  0.02559954  0.09945184
  0.0264158   0.02042906  0.02827603  0.02902685  0.05689565  0.02938313
  0.03595929  0.03929091  0.02076472  0.0342877 ]
PERIOD 1
dates:
[datetime.datetime(2000, 1, 3, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.96571872664
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03256811  0.00384605  0.0320849   0.0492207   0.0804842   0.04060922
  0.01727318  0.00685349  0.04866912  0.04377829  0.02947232  0

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.987192275315
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.0387998   0.00398676  0.03304456  0.05264685  0.0796226   0.04085817
  0.01641127  0.00712861  0.04825314  0.03935848  0.03103772  0.03119458
  0.0057556   0.03499762  0.03854659  0.04139197  0.02457556  0.10416723
  0.02805198  0.02203109  0.02854998  0.03122861  0.05056823  0.02928674
  0.03533825  0.03528345  0.02395049  0.03112635]
PERIOD 15
dates:
[datetime.datetime(2000, 1, 24, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.996295762139
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03989535  0.00421189  0.03377787  0.05409451  0.08169717  0.04257852
  0.01580277  0.00712861  0.04669

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.974562222165
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.04399179  0.00446517  0.03669304  0.06176715  0.08424899  0.04276668
  0.01448799  0.00766982  0.04970906  0.0383128   0.03436419  0.03105231
  0.00352587  0.03051784  0.03386423  0.03866982  0.02147904  0.10051348
  0.02447955  0.02278725  0.02575813  0.02956716  0.04939302  0.02502348
  0.03395901  0.03519157  0.020558    0.02974581]
PERIOD 31
dates:
[datetime.datetime(2000, 2, 15, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.953834908321
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.04210642  0.00428206  0.03598688  0.06138111  0.08078164  0.04134202
  0.01419461  0.0079191   0.04762

Total wealth:
0.911096076723
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.04513086  0.00457773  0.03576055  0.0638904   0.09915084  0.0330091
  0.01265526  0.00615084  0.04371077  0.03714663  0.03255653  0.02951634
  0.00315637  0.02645936  0.02903355  0.03363478  0.02024983  0.09118475
  0.02581791  0.02084335  0.02682644  0.02968645  0.04114098  0.02279917
  0.03165345  0.02131709  0.01753466  0.02650211]
PERIOD 46
dates:
[datetime.datetime(2000, 3, 8, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.935174633996
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.0465056   0.00458711  0.0367202   0.06722003  0.10441031  0.0330091
  0.01276754  0.00633683  0.04605034  0.03887257  0.03377716  0.02921962
  0.00309846  0.02675265  

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
1.04308973009
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.05462052  0.00520398  0.04354186  0.07661057  0.11814339  0.04183393
  0.01430689  0.00741924  0.05360189  0.04341677  0.03861312  0.03602847
  0.0039375   0.02853616  0.03390134  0.03655955  0.02346102  0.10351721
  0.02727348  0.0224111   0.02825085  0.02879918  0.04731907  0.02580941
  0.03484333  0.02074373  0.0174175   0.02696869]
PERIOD 58
dates:
[datetime.datetime(2000, 3, 24, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
1.03327540782
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.05605025  0.00523663  0.04286286  0.07726685  0.1090854   0.04045497
  0.01414752  0.00720095  0.0536018

...

3.38221643887
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.04068658  0.17021777  0.10171751  0.03669737  0.26319661  0.09490301
  0.12389248  0.21294057  0.18437682  0.08191494  0.12213834  0.03330113
  0.06054705  0.22985968  0.09715211  0.07384605  0.14146768  0.17717839
  0.12424508  0.03807751  0.05438845  0.09572091  0.08762778  0.17780238
  0.24774381  0.10335434  0.05257677  0.15464532]
PERIOD 4393
dates:
[datetime.datetime(2017, 6, 19, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
3.37167243492
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03994182  0.16867076  0.10108228  0.03653677  0.26199778  0.09563321
  0.12337382  0.21323144  0.18305329  0.08080533  0.12048077  0.03252641
  0.06001165  0.22899372  0.09664054 

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
3.35333109451
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.03853252  0.16601874  0.10843177  0.03557478  0.2638484   0.09742471
  0.12276294  0.21750143  0.17652853  0.07925649  0.12070101  0.03042197
  0.06652959  0.23263074  0.09486167  0.07317346  0.14151412  0.1743406
  0.12003651  0.03807751  0.05082639  0.09266746  0.08759296  0.17774433
  0.24154325  0.10049041  0.05144135  0.15285745]
PERIOD 4405
dates:
[datetime.datetime(2017, 7, 6, 0, 0)]
---------------------
Need to reallocate -8.881784197e-16 cash amongst experts that are investing
Total wealth:
3.36736010742
Reinvestments:
[ -1.02389294e-17  -4.42341334e-17  -2.87440258e-17  -9.43668528e-18
  -6.91600665e-17  -2.58778938e-17  -3.25047257e-17  -5.76814221e-17
  -4.66164693e-17  -2.11761074e-17  -3.18269822e-17  -7.97533264e-18
  -1.77996525e-17 

Need to reallocate -4.4408920985e-16 cash amongst experts that are investing
Total wealth:
3.37928674399
Reinvestments:
[ -5.19475137e-18  -2.32481117e-17  -1.39291133e-17  -4.84776195e-18
  -3.33719992e-17  -1.29957178e-17  -1.65052232e-17  -2.91869170e-17
  -2.20587994e-17  -1.11795337e-17  -1.64221254e-17  -3.86418575e-18
  -9.01678354e-18  -3.21947297e-17  -1.28879571e-17  -9.53532657e-18
  -1.87862784e-17  -2.19531003e-17  -1.56804032e-17  -5.01902197e-18
  -6.70851497e-18  -1.21399019e-17  -1.17276200e-17  -2.31690857e-17
  -3.20445580e-17  -1.34324785e-17  -6.82716176e-18  -2.01620485e-17]
Final position
[ 0.03952934  0.17690598  0.10599327  0.03688893  0.25394347  0.09889062
  0.12559612  0.22209718  0.16785593  0.08507041  0.12496379  0.02940443
  0.06861301  0.24498506  0.09807062  0.07255885  0.14295376  0.16705162
  0.11931967  0.03819213  0.05104829  0.09237831  0.08924106  0.17630463
  0.24384234  0.10221414  0.05195113  0.15342265]
PERIOD 4417
dates:
[datetime.datetime(2

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
3.62018140821
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.18408217  0.18408217  0.10917493  0.03686578  0.27109961  0.09987953
  0.1331774   0.22662313  0.17803781  0.08368339  0.12420466  0.02963569
  0.0695907   0.27737186  0.09552139  0.07287195  0.13760155  0.16416806
  0.12692746  0.03855181  0.0570629   0.09271372  0.09433624  0.17992709
  0.24086978  0.10599298  0.052878    0.15324963]
PERIOD 4427
dates:
[datetime.datetime(2017, 8, 7, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
3.47546234236
Reinvestments:
[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]
Final position
[ 0.04202989  0.18619968  0.10878012  0.03666894  0.270087    0.09998423
  0.1328291   0.22676275  0.178037

Need to reallocate -4.4408920985e-16 cash amongst experts that are investing
Total wealth:
3.45233112433
Reinvestments:
[ -5.15703568e-18  -2.44740550e-17  -1.36075149e-17  -4.68859628e-18
  -3.30447065e-17  -1.27836101e-17  -1.73253673e-17  -2.94434189e-17
  -2.25105420e-17  -1.09190735e-17  -1.54091450e-17  -3.63517596e-18
  -7.89474682e-18  -3.59346976e-17  -1.23549585e-17  -9.41562184e-18
  -1.78323634e-17  -2.12915074e-17  -1.62038645e-17  -4.98738277e-18
  -7.28768281e-18  -1.14851237e-17  -1.18336585e-17  -2.38034837e-17
  -3.04847783e-17  -1.37655782e-17  -6.77362388e-18  -1.97418968e-17]
Final position
[ 0.04009058  0.19026029  0.10578426  0.03644895  0.25688818  0.09937926
  0.13468669  0.22889192  0.17499602  0.08488442  0.11979006  0.02825971
  0.06137343  0.27935485  0.09604694  0.07319665  0.13862805  0.1655193
  0.12596817  0.03877171  0.05665414  0.08928488  0.09199437  0.1850473
  0.2369874   0.10701303  0.05265787  0.15347269]
PERIOD 4443
dates:
[datetime.datetime(201

In [19]:
## Run buy-and-hold simulation, where initial weights are determined randomly
start = time.time()
s = SimulationEnv(initial_wealth, stocks, "data/djia_20000101_20170831/", "2000-01-01", "2017-08-31", RandomWeightedBuyHold, Dummy, True)
s.setup_params(agent_args={})
s.run()

years = 17. + 11./12
ar = ((s.wealth)/initial_wealth)**(1/years) - 1
end = time.time()

print("Initial wealth: ${}".format(initial_wealth))
print("Final wealth: ${}".format(s.wealth))
print("Annualized return: {}".format(ar))
print("Time: {}s".format(int(end-start)))

['INTC', 'AAPL', 'JPM', 'CSCO', 'GS', 'AXP', 'CAT', 'UNH', 'HD', 'MSFT', 'DIS', 'GE', 'NKE', 'BA', 'DD', 'MRK', 'UTX', 'IBM', 'CVX', 'PFE', 'VZ', 'XOM', 'WMT', 'MCD', 'MMM', 'PG', 'KO', 'JNJ']
Initial weights:
[[ 0.01285855  0.0586663   0.01429271  0.02224791  0.00033045  0.06420646
   0.00589371  0.05289019  0.06185787  0.01937392  0.00547484  0.01736737
   0.02787324  0.03560289  0.14850231  0.01571774  0.0463293   0.00917622
   0.06277133  0.01001492  0.04130021  0.08139765  0.01086635  0.00319017
   0.01186536  0.03019927  0.06048766  0.06924513]]
PERIOD 1
dates:
[datetime.datetime(2000, 1, 3, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.970831670783
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]]
Final position
[[ 0.01225848  0.05371892  0.01398281  0.02099248  0.00030964  0.06177702
   0.00581735  0.05221122  0.05550982  0.01871904  0

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.993834788153
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]]
Final position
[[ 0.01426264  0.05774915  0.01547421  0.02206268  0.00033068  0.06534532
   0.00548194  0.05417923  0.05444707  0.0165167   0.00671162  0.01637628
   0.0286726   0.04091808  0.13922663  0.01692161  0.04225232  0.00923554
   0.06586373  0.01095735  0.0400498   0.08679228  0.01007426  0.00287784
   0.012108    0.02841857  0.06781069  0.06271795]]
PERIOD 17
dates:
[datetime.datetime(2000, 1, 26, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.982838321852
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]]
Final position
[[ 0.01450355  0.05764957  0.01591807  0.0219392   0.00033349  0.06661297
   0.00543559  0.053

Need to reallocate 1.11022302463e-16 cash amongst experts that are investing
Total wealth:
0.916133668187
Reinvestments:
[[  1.89733931e-18   6.90691376e-18   1.97518319e-18   3.26478509e-18
    3.86573946e-20   7.60672051e-18   5.32175862e-19   6.67784055e-18
    6.90638313e-18   2.01306921e-18   8.41108483e-19   1.87667065e-18
    2.38666886e-18   4.29665007e-18   1.41479055e-17   1.83773370e-18
    4.34603268e-18   1.10710372e-18   6.73104220e-18   1.33244230e-18
    4.70638889e-18   9.35991289e-18   1.10495991e-18   3.40851020e-19
    1.26361976e-18   3.20942307e-18   7.24032139e-18   7.07439940e-18]]
Final position
[[ 0.01565646  0.05699446  0.01629881  0.02694035  0.00031899  0.06276912
   0.00439141  0.05510419  0.05699008  0.01661144  0.00694066  0.01548591
   0.01969431  0.03545509  0.11674567  0.01516461  0.03586259  0.0091356
   0.0555432   0.01099505  0.03883617  0.07723612  0.00911791  0.00281263
   0.01042714  0.02648351  0.05974567  0.05837652]]
PERIOD 29
dates:
[datetim

Need to reallocate -1.11022302463e-16 cash amongst experts that are investing
Total wealth:
0.892630968382
Reinvestments:
[[ -2.13117629e-18  -8.49413983e-18  -2.01197665e-18  -3.37122408e-18
   -4.41586776e-20  -6.89152393e-18  -5.29195377e-19  -6.68477213e-18
   -6.56540155e-18  -1.87732702e-18  -7.90557087e-19  -1.89195335e-18
   -2.02660857e-18  -4.01502246e-18  -1.38423192e-17  -1.74274659e-18
   -4.70247205e-18  -9.87339909e-19  -7.08364650e-18  -1.24894165e-18
   -4.73887586e-18  -9.88981426e-18  -9.91234483e-19  -3.12880584e-19
   -1.35523288e-18  -3.10068252e-18  -6.82107269e-18  -6.88000624e-18]]
Final position
[[ 0.01713488  0.06829378  0.0161765   0.027105    0.00035504  0.05540858
   0.00425479  0.05374627  0.05278652  0.01509391  0.00635616  0.0152115
   0.01629415  0.0322812   0.1112937   0.01401187  0.03780837  0.00793832
   0.05695326  0.01004162  0.03810106  0.07951514  0.00796963  0.00251559
   0.01089621  0.02492981  0.05484214  0.05531597]]
PERIOD 41
dates:
[dateti

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.93118814278
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]]
Final position
[[ 0.01920467  0.06551087  0.01795197  0.02778416  0.00043654  0.05872082
   0.00483421  0.05079426  0.06000588  0.0165167   0.0067446   0.01624397
   0.01976042  0.03378369  0.1209094   0.01465408  0.04065088  0.00871037
   0.0630535   0.0112795   0.04104845  0.08063375  0.00907805  0.00272167
   0.01086459  0.01627994  0.05303655  0.05997464]]
PERIOD 53
dates:
[datetime.datetime(2000, 3, 17, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
0.931950980422
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]]
Final position
[[ 0.01995866  0.0644627   0.01707607  0.02759894  0.00042492  0.05806655
   0.00469637  0.0521

...

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
7.13411255492
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]]
Final position
[[  1.55816173e-02   2.50924168e+00   4.17570914e-02   1.54409370e-02
    9.60638719e-04   1.39029252e-01   4.05839303e-02   1.59608579e+00
    2.04187513e-01   3.58412564e-02   2.40471152e-02   1.64211030e-02
    3.05461816e-01   2.41838937e-01   3.50516169e-01   2.93625492e-02
    2.52389146e-01   1.60871023e-02   2.86201940e-01   1.80204965e-02
    7.92184758e-02   2.63395138e-01   1.74961070e-02   1.90635245e-02
    7.87011836e-02   7.85018134e-02   1.53916457e-01   3.04763776e-01]]
PERIOD 4384
dates:
[datetime.datetime(2017, 6, 6, 0, 0)]
---------------------
Need to reallocate -8.881784197e-16 cash amongst experts that are investing
Total wealth:
7.17531904878
Reinvestments:
[[ -1.93567023e-18  -3.12450156e-16  -5.22798362e-18  -1.91434476e-18
 

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
7.09028561142
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]]
Final position
[[  1.48182776e-02   2.36594928e+00   4.38006521e-02   1.55828214e-02
    9.84102789e-04   1.45024172e-01   4.03083245e-02   1.65306757e+00
    2.05882455e-01   3.47243060e-02   2.37553587e-02   1.63320143e-02
    3.04996173e-01   2.58272329e-01   3.51726933e-01   3.01981711e-02
    2.56696486e-01   1.63014281e-02   2.86971226e-01   1.91387001e-02
    7.74785351e-02   2.62973498e-01   1.67402255e-02   1.95135462e-02
    8.13103801e-02   7.87051401e-02   1.52109926e-01   3.16923579e-01]]
PERIOD 4396
dates:
[datetime.datetime(2017, 6, 22, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
7.09592881382
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
7.10671490619
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]]
Final position
[[  1.46285209e-02   2.36432465e+00   4.69769449e-02   1.53527796e-02
    1.01625394e-03   1.48951282e-01   4.20163043e-02   1.64819258e+00
    1.99420489e-01   3.45908650e-02   2.38473755e-02   1.56384224e-02
    3.38638880e-01   2.67117095e-01   3.57045646e-01   2.85149044e-02
    2.59575051e-01   1.61736773e-02   2.83317116e-01   1.86385990e-02
    7.31627999e-02   2.61416674e-01   1.62858100e-02   1.95274125e-02
    8.03295368e-02   7.67072336e-02   1.49612448e-01   3.05695562e-01]]
PERIOD 4408
dates:
[datetime.datetime(2017, 7, 11, 0, 0)]
---------------------
Need to reallocate 1.7763568394e-15 cash amongst experts that are investing
Total wealth:
7.14040446625
Reinvestments:
[[  3.67462095e-18   5.89034517e-16   1.16464214e-17   3.82799307e-18


Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
7.29367146355
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]]
Final position
[[  1.52279797e-02   2.42882247e+00   4.61925620e-02   1.55651211e-02
    1.00129783e-03   1.50083992e-01   4.46136810e-02   1.69428347e+00
    1.96083573e-01   3.60982538e-02   2.52528641e-02   1.51345309e-02
    3.41490944e-01   3.12441661e-01   3.64774038e-01   2.93245191e-02
    2.49762719e-01   1.52340224e-02   2.97054370e-01   1.86273608e-02
    8.17772121e-02   2.58173291e-01   1.76911732e-02   1.96459056e-02
    7.65211060e-02   8.03711169e-02   1.55282399e-01   3.07139830e-01]]
PERIOD 4421
dates:
[datetime.datetime(2017, 7, 28, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
7.29489290866
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.

Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
7.41788690651
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.  0.  0.  0.  0.  0.  0.  0.  0.]]
Final position
[[  1.52810790e-02   2.57521060e+00   4.58737483e-02   1.53280888e-02
    9.91491284e-04   1.52367109e-01   4.42383161e-02   1.70802210e+00
    1.98189008e-01   3.59725387e-02   2.32824242e-02   1.46721363e-02
    3.34448093e-01   3.06935059e-01   3.51222061e-01   2.82861997e-02
    2.45389673e-01   1.50117906e-02   2.93951674e-01   1.86949540e-02
    8.16919209e-02   2.49752094e-01   1.77771938e-02   1.99030608e-02
    7.86781951e-02   8.20282533e-02   1.54776153e-01   3.09911892e-01]]
PERIOD 4435
dates:
[datetime.datetime(2017, 8, 17, 0, 0)]
---------------------
Need to reallocate 0.0 cash amongst experts that are investing
Total wealth:
7.37646350358
Reinvestments:
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.  0.
   0.  0.